In [1]:
%config IPCompleter.greedy=True
import numpy as np
import pandas as pd
import psycopg2
import matplotlib.pyplot as plt
import time
import re
import scipy
from datetime import time, timedelta
import seaborn as sns
import datetime as dt
pd.set_option('display.max_columns', 100)

In [2]:
'''
*****自定义数据提取的代码*****
输入：
    sql:常规sql代码

输出：
    dataframe格式数据表格
    
备注：
    当sql代码出错的时候，函数会返回sql的报错内容
'''
def get_data_MIMIC(sql):
    conn = psycopg2.connect(database="mimiciv2_2",user="postgres",
                           password="postgres",
                            host="10.245.99.98",
                            #ost="172.16.2.76",
                            port="5433")
    cur = conn.cursor()
    try:
        cur.execute(sql)
        #获取表的所有字段名称
        coloumns = [row[0] for row in cur.description]
        result = [[str(item) for item in row] for row in cur.fetchall()]
        return pd.DataFrame(result,columns=coloumns)
    except Exception as ex:
        print(ex)
    finally:
            conn.close()

In [3]:
def trans_id(df):
    for i in ['subject_id','hadm_id','stay_id']:
        if i in df.columns.tolist():
            if df[i].dtype == object:
                if ((df[i]== 'None')|(df[i]== 'Null')).any():
                    df[i].replace('None',np.nan,inplace = True)
                    df[i].replace('Null',np.nan,inplace = True)
                    df[i] = df[i].astype(float)
                else:
                    df[i] = df[i].astype(float)

In [4]:
def trans_float(df):
    for i in df.columns.tolist():
        if df[i].dtype == object:
            if ((df[i]== 'None')|(df[i]== 'Null')).any():
                df[i].replace('None',np.nan,inplace = True)
                df[i].replace('Null',np.nan,inplace = True)
                df[i] = df[i].astype(float)
            else:
                df[i] = df[i].astype(float)

In [5]:
def trans_time(t):
    if t == 'None':
        return np.datetime64('NaT')
    elif pd.isna(t):
        return np.datetime64('NaT')
    else:
        return np.datetime64(t)

In [6]:
def lookup_miss(df):
    nadf = pd.DataFrame(columns=['nan_nums','nan_ratios'])
    for i in df.columns:
        nadf.loc[i,'nan_nums'] = pd.isna(df[i]).sum()
        nadf.loc[i,'nan_ratios'] = (nadf.loc[i,'nan_nums']/df.shape[0])*100
    return nadf.sort_values(by = 'nan_ratios', ascending = False)

In [7]:
final_cohort = pd.read_csv('final_cohort.csv')

In [8]:
final_cohort['admittime'] = final_cohort['admittime'].apply(lambda x:trans_time(x))
final_cohort['dischtime'] = final_cohort['dischtime'].apply(lambda x:trans_time(x))
final_cohort['icu_intime'] = final_cohort['icu_intime'].apply(lambda x:trans_time(x))
final_cohort['icu_outtime'] = final_cohort['icu_outtime'].apply(lambda x:trans_time(x))

In [9]:
#90天内是否住过院

In [10]:
adm_pre = pd.merge(final_cohort[['subject_id','admittime','dischtime']].rename(columns = {'admittime':'admittime_pre', 'dischtime':'dischtime_pre'}),
         final_cohort[['subject_id','hadm_id','admittime']],how = 'left', on = ['subject_id'])

adm_pre['pre_now']= (adm_pre['admittime_pre'] - adm_pre['admittime']).dt.days

adm_pre90 = adm_pre[(adm_pre['pre_now']<0)&(adm_pre['pre_now']>=-90)][['hadm_id']]

adm_pre90['before_adm_90d'] = 1

In [11]:
icustay_detail = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.icustay_detail
''')

# Lab

## chemistry

In [12]:
chemistry = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.chemistry_nea
''')

In [13]:
chemistry.replace({'None':np.nan},inplace= True)
trans_id(chemistry)

In [14]:
che_fc = pd.merge(final_cohort['stay_id'],chemistry,how = 'left',on = ['stay_id']) 

In [15]:
lookup_miss(che_fc)

nan_nums nan_ratios
globulin         46723  98.050449
total_protein    46127  96.799715
albumin          22774  47.792328
calcium           2877   6.037522
aniongap           114   0.239234
potassium           87   0.182574
bicarbonate         77   0.161588
creatinine          42   0.088139
bun                 40   0.083942
glucose             40   0.083942
chloride            37   0.077646
sodium              37   0.077646
stay_id              0        0.0

In [16]:
#che_fc = che_fc[['stay_id','calcium','aniongap','potassium','bicarbonate','glucose','bun','sodium','chloride','creatinine']]

## blood gas

In [201]:
bg = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.bg_art_nea
''')

bg.replace({'None':np.nan},inplace= True)
trans_id(bg)

bg_fc = pd.merge(final_cohort['stay_id'],bg,how = 'left',on = ['stay_id']) 

In [202]:
lookup_miss(bg_fc)

nan_nums nan_ratios
methemoglobin        47462  99.588736
carboxyhemoglobin    47430  99.521591
bicarbonate          47401  99.460741
aado2                45545  95.566327
fio2                 43134  90.507365
so2                  43084  90.402451
fio2_chartevents     40358   84.68253
aado2_calc           37758  79.226992
pao2fio2ratio        37758  79.226992
lactate              30852  64.736246
pco2                 21535  45.186537
ph                   21535  45.186537
totalco2             21535  45.186537
po2                  21534  45.184439
baseexcess           21534  45.184439
stay_id                  0        0.0

In [19]:
#bg_fc = bg_fc[['stay_id','pco2','po2','totalco2','baseexcess','ph','lactate']]

## blood differential

In [20]:
bd = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.blood_differential_nea
''')

bd.replace({'None':np.nan},inplace= True)
trans_float(bd)
bd_fc = pd.merge(final_cohort['stay_id'],bd,how = 'left',on = ['stay_id']) 

In [21]:
for i in bd.columns[2:]:
    bd[i] = bd[i].round(2)

In [22]:
lookup_miss(bd_fc)

nan_nums nan_ratios
nrbc                     45100  94.610753
atypical_lymphocytes     40675  85.327991
metamyelocytes           40559  85.084646
bands                    40076  84.071409
immature_granulocytes    36504   76.57807
eosinophils              12756  26.759529
monocytes_abs            12755  26.757431
neutrophils_abs          12755  26.757431
basophils                12755  26.757431
monocytes                12755  26.757431
neutrophils              12755  26.757431
eosinophils_abs          12755  26.757431
basophils_abs            12755  26.757431
wbc                      12724    26.6924
specimen_id              12723  26.690302
lymphocytes              12723  26.690302
lymphocytes_abs          12723  26.690302
stay_id                      0        0.0

In [23]:
# mistable = lookup_miss(bd_fc)
# bd_fc = bd_fc[mistable[mistable['nan_ratios']<30].index]
# bd_fc.drop(columns = ['wbc'], inplace = True)

## cardiac marker

In [24]:
cm = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.cardiac_marker_nea
''')

cm.replace({'None':np.nan},inplace= True)
trans_id(cm)

cm_fc = pd.merge(final_cohort['stay_id'],cm,how = 'left',on = ['stay_id']) 

In [25]:
cm

stay_id  troponin_i troponin_t ck_mb
0      30000153.0         NaN        NaN  20.0
1      30000213.0         NaN       0.03   NaN
2      30000484.0         NaN       0.18   NaN
3      30000646.0         NaN       0.02   1.0
4      30001336.0         NaN        1.6   2.0
...           ...         ...        ...   ...
25535  39998871.0         NaN       0.15   3.0
25536  39999172.0         NaN       0.01   NaN
25537  39999286.0         NaN        NaN   3.0
25538  39999301.0         NaN        NaN   1.0
25539  39999810.0         NaN       0.02   6.0

[25540 rows x 4 columns]

In [26]:
lookup_miss(cm_fc)

nan_nums nan_ratios
troponin_i    47652      100.0
troponin_t    34647  72.708386
ck_mb         31679  66.479896
stay_id           0        0.0

## coagulation

In [27]:
co = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.coagulation_nea
''')

co.replace({'None':np.nan},inplace= True)
trans_id(co)

co_fc = pd.merge(final_cohort['stay_id'],co,how = 'left',on = ['stay_id']) 

In [28]:
lookup_miss(co_fc)

nan_nums nan_ratios
thrombin         47533  99.750273
d_dimer          47508  99.697809
fibrinogen       33786  70.901536
bleeding_time    33348  69.982372
ptt               3086   6.476119
pt                2891   6.066902
inr               2890   6.064803
stay_id              0        0.0

In [29]:
#co_fc = co_fc[['stay_id','ptt','pt','inr']]

## complete blood count

In [30]:
cbc = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.complete_blood_count_nea
''')

cbc.replace({'None':np.nan},inplace= True)
trans_id(cbc)

cbc_fc = pd.merge(final_cohort['stay_id'],cbc,how = 'left',on = ['stay_id']) 

In [31]:
lookup_miss(cbc_fc)

nan_nums nan_ratios
rdwsd         47652      100.0
rdw              63   0.132209
mch              58   0.121716
mchc             54   0.113322
mcv              53   0.111223
rbc              52   0.109124
hemoglobin       51   0.107026
wbc              48    0.10073
platelet         46   0.096533
hematocrit       39   0.081843
stay_id           0        0.0

In [32]:
cbc_fc = cbc_fc.drop(columns = 'rdwsd')

## enzyme

In [33]:
enz = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.enzyme_nea
''')

enz.replace({'None':np.nan},inplace= True)
trans_id(enz)

enz_fc = pd.merge(final_cohort['stay_id'],enz,how = 'left',on = ['stay_id']) 

In [34]:
lookup_miss(enz_fc)

nan_nums nan_ratios
ggt                   47184   99.01788
bilirubin_indirect    44740  93.889029
bilirubin_direct      44632  93.662386
amylase               43275  90.814656
ck_mb                 31679  66.479896
ck_cpk                30358  63.707714
ld_ldh                29965  62.882985
bilirubin_total       17583  36.898766
alp                   17514  36.753966
alt                   17403  36.521027
ast                   17255  36.210442
stay_id                   0        0.0

In [35]:
lab_fc = che_fc.merge(bg_fc,how = 'left' , on = 'stay_id').\
merge(bd_fc, how = 'left', on = 'stay_id').\
merge(co_fc, how = 'left', on = 'stay_id').\
merge(cbc_fc, how = 'left', on = 'stay_id').\
merge(cm_fc, how = 'left', on = 'stay_id').\
merge(enz_fc, how = 'left', on = 'stay_id').\
drop_duplicates()

# Vitals

In [36]:
vs = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.vitalsign_1sttime
''')

vs.replace({'None':np.nan},inplace= True)
trans_id(vs)

vs_fc = pd.merge(final_cohort['stay_id'],vs,how = 'left',on = ['stay_id']) 

In [37]:
lookup_miss(vs_fc)

nan_nums nan_ratios
sbp_ni         47652      100.0
dbp_ni         47652      100.0
mbp_ni         47652      100.0
temperature     1612   3.382859
glucose          250   0.524637
resp_rate        199   0.417611
dbp              191   0.400823
sbp              185   0.388231
mbp              131    0.27491
spo2              75   0.157391
heart_rate        66   0.138504
stay_id            0        0.0

In [38]:
vs_fc= vs_fc[['stay_id','heart_rate','spo2','sbp','dbp','mbp','resp_rate','temperature']]

## GCS

In [39]:
gcs = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.gcs_1sttime
''')

gcs.replace({'None':np.nan},inplace= True)
trans_id(gcs)

gcs_fc = pd.merge(final_cohort['stay_id'],gcs,how = 'left',on = ['stay_id']) 

In [40]:
vs_fc = pd.merge(vs_fc, gcs_fc, how = 'left', on = 'stay_id')

In [41]:
trans_float(vs_fc)

In [42]:
vs_fc['temperature'] = round(vs_fc['temperature'].astype(float),2)

In [43]:
vs_fc.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 47954 entries, 0 to 47953
Data columns (total 13 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   stay_id      47954 non-null  float64
 1   heart_rate   47888 non-null  float64
 2   spo2         47879 non-null  float64
 3   sbp          47766 non-null  float64
 4   dbp          47760 non-null  float64
 5   mbp          47821 non-null  float64
 6   resp_rate    47755 non-null  float64
 7   temperature  46319 non-null  float64
 8   gcs          47886 non-null  float64
 9   gcs_motor    47233 non-null  float64
 10  gcs_verbal   47517 non-null  float64
 11  gcs_eyes     47729 non-null  float64
 12  gcs_unable   47886 non-null  float64
dtypes: float64(13)
memory usage: 5.1 MB


In [44]:
lab_vs_fc = lab_fc.merge(vs_fc, how = 'left', on = 'stay_id').drop_duplicates()
#lab_vs_fc = final_cohort.merge(lab_vs_fc,how = 'left', on = ['stay_id'])

# 缺失率与耐药率

In [45]:
# for i in lab1stfc_nadf.index:
#     na_num = lab_vs_fc[pd.isna(lab_vs_fc[i])].shape[0]
#     nona_num = lab_vs_fc[~pd.isna(lab_vs_fc[i])].shape[0]
#     if na_num > 0:
#         na_nomdr_num = lab_vs_fc[pd.isna(lab_vs_fc[i])].stay_chart_included_mdr.value_counts()[0]
#         nona_nomdr_num = lab_vs_fc[~pd.isna(lab_vs_fc[i])].stay_chart_included_mdr.value_counts()[0]
#         lab1stfc_nadf.loc[i,'na_mdr_ratios'] = (na_num-na_nomdr_num)/na_num*100
#         lab1stfc_nadf.loc[i,'nona_mdr_ratios'] = (nona_num-nona_nomdr_num)/nona_num*100
#     if na_num == 0:
#         lab1stfc_nadf.loc[i,'na_mdr_ratios'] = np.nan
#         lab1stfc_nadf.loc[i,'nona_mdr_ratios'] = np.nan

In [46]:
#lab1stfc_nadf.sort_values(by = ['nan_ratios'],ascending = False)[50:100]

# 抗菌素使用天数

## 在住ICU之前使用抗生素

In [47]:
antibiotic_beforeicu = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.antibiotic_beforeicu
''')

In [48]:
antibiotic_beforeicu.replace({'None':np.nan},inplace= True)

In [49]:
antibiotic_beforeicu['starttime'] = antibiotic_beforeicu['starttime'].apply(lambda x:trans_time(x))
antibiotic_beforeicu['stoptime'] = antibiotic_beforeicu['stoptime'].apply(lambda x:trans_time(x))
antibiotic_beforeicu['startdate'] = antibiotic_beforeicu['startdate'].apply(lambda x:trans_time(x))
antibiotic_beforeicu['enddate'] = antibiotic_beforeicu['enddate'].apply(lambda x:trans_time(x))

In [50]:
trans_id(antibiotic_beforeicu)
ant_bef_mer = pd.merge(antibiotic_beforeicu,final_cohort[['subject_id','stay_id','icu_intime']],how = 'right', on = ['subject_id','stay_id'])

In [51]:
ant_bef_mer.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 93201 entries, 0 to 93200
Data columns (total 11 columns):
 #   Column      Non-Null Count  Dtype         
---  ------      --------------  -----         
 0   subject_id  93201 non-null  float64       
 1   hadm_id     58227 non-null  float64       
 2   stay_id     93201 non-null  float64       
 3   antibiotic  58227 non-null  object        
 4   route       58227 non-null  object        
 5   starttime   58227 non-null  datetime64[ns]
 6   stoptime    58226 non-null  datetime64[ns]
 7   startdate   58227 non-null  datetime64[ns]
 8   enddate     58226 non-null  datetime64[ns]
 9   ini_days    58226 non-null  object        
 10  icu_intime  93201 non-null  datetime64[ns]
dtypes: datetime64[ns](5), float64(3), object(3)
memory usage: 8.5+ MB


In [52]:
ant_bef_mer_beficu = ant_bef_mer[(ant_bef_mer['icu_intime'] - ant_bef_mer['starttime']).dt.total_seconds()>0]
ant_bef_mer_beficu = ant_bef_mer_beficu[['subject_id','stay_id','startdate','enddate']].drop_duplicates()

In [53]:
ant_bef_mer_beficu = ant_bef_mer_beficu[~pd.isna(ant_bef_mer_beficu['enddate'])]

In [54]:
def ant_duration(df):
    days_list = []
    for i in range(df.size()):
        once_days = (df.loc[i,'enddate']-df.loc[i,'startdate']).days + 1
        for j in range(int(once_days)):
            mid_day = df.loc[i,'startdate'] + pd.to_timedelta(j,'day')
            days_list.append(mid_day)
    return len(list(set(days_list)))

In [55]:
ant_dur_df = pd.DataFrame()
for i in set(ant_bef_mer_beficu.stay_id):
    temp = pd.DataFrame()
    ini_df = ant_bef_mer_beficu[ant_bef_mer_beficu['stay_id'] == i].reset_index()
    days_list = []
    for j in range(len(ini_df)):
        once_days = (ini_df.loc[j,'enddate']-ini_df.loc[j,'startdate']).days + 1
        for m in range(once_days):
            mid_day = ini_df.loc[j,'startdate'] + pd.to_timedelta(m,'day')
            days_list.append(mid_day)
    temp.loc[0,'stay_id'] = i
    temp.loc[0,'ant_duration'] = len(list(set(days_list)))
    ant_dur_df = ant_dur_df.append(temp,ignore_index=True)

/tmp/ipykernel_2822985/768244566.py:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ant_dur_df = ant_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/768244566.py:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ant_dur_df = ant_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/768244566.py:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ant_dur_df = ant_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/768244566.py:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ant_dur_df = ant_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/768244566.py:13: FutureWarning: The frame.append method i

In [56]:
ant_dur_df[pd.isna(ant_dur_df.ant_duration)]

Empty DataFrame
Columns: [stay_id, ant_duration]
Index: []

In [57]:
ant_dur_df.ant_duration.value_counts().head(20)

2.0     3292
1.0     3028
3.0     1216
4.0      916
5.0      648
6.0      640
7.0      425
8.0      341
9.0      240
10.0     225
11.0     205
12.0     149
13.0     139
14.0     130
15.0      99
17.0      92
16.0      78
18.0      74
19.0      65
20.0      63
Name: ant_duration, dtype: int64

## 在住ICU第一天使用抗菌素

In [58]:
antibiotic = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.antibiotic
''')

In [59]:
trans_id(antibiotic)
antibiotic.replace({'None':np.nan},inplace= True)

antibiotic['starttime'] = antibiotic['starttime'].apply(lambda x:trans_time(x))
antibiotic['stoptime'] = antibiotic['stoptime'].apply(lambda x:trans_time(x))

In [60]:
ant_co = pd.merge(antibiotic,final_cohort[['subject_id','hadm_id','icu_intime']],how = 'right', on = ['subject_id','hadm_id'])

In [61]:
ant_co_1stday = ant_co[(ant_co['starttime']>(ant_co['icu_intime']-pd.to_timedelta(6,'hour')))&\
                       (ant_co['starttime']<(ant_co['icu_intime']+pd.to_timedelta(1,'day')))]

In [62]:
final_cohort[final_cohort['stay_id']==37510196.0]

subject_id     hadm_id     stay_id gender           admittime  \
2  10001884.0  26184834.0  37510196.0      F 2131-01-07 20:39:00   

            dischtime  los_hospital  admission_age                    race  \
2 2131-01-20 05:15:00     12.358333      77.018296  BLACK/AFRICAN AMERICAN   

   hospital_expire_flag  hospstay_seq  first_hosp_stay          icu_intime  \
2                     1             1             True 2131-01-11 04:20:05   

          icu_outtime  los_icu  icustay_seq  first_icu_stay  \
2 2131-01-20 08:27:30     9.17            1            True   

   spec_type_desc_URINE  spec_type_desc_BLOOD CULTURE  spec_type_desc_SWAB  \
2                     1                             1                    1   

   spec_type_desc_SPUTUM  spec_type_desc_TISSUE  \
2                      1                      0   

   spec_type_desc_BRONCHOALVEOLAR LAVAGE  spec_type_desc_ABSCESS  \
2                                      0                       0   

  firsthospmdrcharttime firsthospmdrstoretime firsthospmdrorgname  \
2                   NaN                   NaN                 NaN   

  firsthospmdrRAB  last  previous_mdrpos_lessthan14d  \
2             NaN   1.0                            0   

   previous_mdrneg_lessthan14d  previous_mdrpos_lessthan90d  \
2                            0                            0   

   previous_mdrneg_lessthan90d  stay_chart_included  stay_chart_included_mdr  \
2                            0                    1                        0   

   stay_chart_included_mdr_neg_tot  stay_chart_included_mdr_pos_tot  \
2                                0                                0   

   icustay_rank  los_icu_exc  los_hosp_beforeicu  
2           1.0            0            3.320197

In [63]:
ant_1stday = ant_co_1stday[['subject_id','hadm_id','stay_id']].drop_duplicates()

In [64]:
ant_1stday['ant_1stday'] = 1

# 免疫抑制剂

## 住ICU之前

In [65]:
immu = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.immunosuppressant
''')

In [66]:
immu.replace({'None':np.nan},inplace= True)

In [67]:
immu.replace({'None':np.nan},inplace= True)

immu['starttime'] = immu['starttime'].apply(lambda x:trans_time(x))
immu['stoptime'] = immu['stoptime'].apply(lambda x:trans_time(x))

immu['startdate'] = immu['starttime'].dt.date
immu['enddate'] = immu['stoptime'].dt.date

immu = immu[immu['starttime']<immu['stoptime']]

In [68]:
trans_id(immu)

In [69]:
immu_co = pd.merge(immu[['subject_id','starttime','stoptime']].drop_duplicates(),\
         final_cohort[['subject_id','hadm_id','stay_id','admittime','icu_intime']],how = 'left', on = ['subject_id'])

In [70]:
immu_co

subject_id           starttime            stoptime     hadm_id  \
0       16944007.0 2117-02-23 19:00:00 2117-02-24 18:00:00  28612927.0   
1       16931776.0 2180-07-23 12:00:00 2180-07-23 19:00:00         NaN   
2       16931776.0 2180-07-24 08:00:00 2180-07-27 10:00:00         NaN   
3       16931776.0 2180-07-25 16:00:00 2180-07-26 15:00:00         NaN   
4       16931776.0 2180-07-26 10:00:00 2180-07-27 13:00:00         NaN   
...            ...                 ...                 ...         ...   
274852  11911069.0 2197-02-15 18:00:00 2197-02-17 15:00:00  21813052.0   
274853  11911069.0 2197-02-15 18:00:00 2197-02-17 15:00:00  21813052.0   
274854  11911069.0 2197-02-15 18:00:00 2197-02-17 15:00:00  24424592.0   
274855  16603070.0 2149-04-16 20:00:00 2149-04-18 20:00:00         NaN   
274856  10695080.0 2178-01-18 20:00:00 2178-01-19 23:00:00         NaN   

           stay_id           admittime          icu_intime  
0       38904419.0 2117-02-23 11:33:00 2117-02-28 02:03:29  
1              NaN                 NaT                 NaT  
2              NaN                 NaT                 NaT  
3              NaN                 NaT                 NaT  
4              NaN                 NaT                 NaT  
...            ...                 ...                 ...  
274852  33566488.0 2197-01-30 20:11:00 2197-01-30 20:12:09  
274853  36447338.0 2197-01-30 20:11:00 2197-02-13 16:51:16  
274854  38407575.0 2196-08-23 23:53:00 2196-08-30 11:10:45  
274855         NaN                 NaT                 NaT  
274856         NaN                 NaT                 NaT  

[274857 rows x 7 columns]

In [71]:
#限定在住ICU之前90天内
immu_co = immu_co[((immu_co['starttime']-immu_co['icu_intime']).dt.total_seconds()<0)&\
        ((immu_co['starttime']-immu_co['icu_intime']).dt.total_seconds()>=-24*3600*90)]

In [72]:
immu_co['endtime'] = immu_co[['icu_intime','stoptime']].apply(lambda x: x[0] if x[0]<x[1] else x[1], axis = 1)

/tmp/ipykernel_2822985/397005142.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  immu_co['endtime'] = immu_co[['icu_intime','stoptime']].apply(lambda x: x[0] if x[0]<x[1] else x[1], axis = 1)


In [73]:
immu_co['startdate']= immu_co['starttime'].dt.date
immu_co['enddate']= immu_co['endtime'].dt.date

/tmp/ipykernel_2822985/2385543163.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  immu_co['startdate']= immu_co['starttime'].dt.date
/tmp/ipykernel_2822985/2385543163.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  immu_co['enddate']= immu_co['endtime'].dt.date


In [74]:
immu_tocount = immu_co[['subject_id','hadm_id','stay_id','startdate','enddate']].drop_duplicates()
immu_tocount = immu_tocount[~pd.isna(immu_tocount['enddate'])]

In [75]:
def immu_duration(df):
    days_list = []
    for i in range(df.size()):
        once_days = (df.loc[i,'enddate']-df.loc[i,'startdate']).days + 1
        for j in range(int(once_days)):
            mid_day = df.loc[i,'startdate'] + pd.to_timedelta(j,'day')
            days_list.append(mid_day)
    return len(list(set(days_list)))

immu_dur_df = pd.DataFrame()
for i in set(immu_tocount.stay_id):
    temp = pd.DataFrame()
    ini_df = immu_tocount[immu_tocount['stay_id'] == i].reset_index()
    days_list = []
    for j in range(len(ini_df)):
        once_days = (ini_df.loc[j,'enddate']-ini_df.loc[j,'startdate']).days + 1
        for m in range(once_days):
            mid_day = ini_df.loc[j,'startdate'] + pd.to_timedelta(m,'day')
            days_list.append(mid_day)
    temp.loc[0,'stay_id'] = i
    temp.loc[0,'immu_duration'] = len(list(set(days_list)))
    immu_dur_df = immu_dur_df.append(temp,ignore_index=True)

/tmp/ipykernel_2822985/2461970791.py:22: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  immu_dur_df = immu_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/2461970791.py:22: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  immu_dur_df = immu_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/2461970791.py:22: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  immu_dur_df = immu_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/2461970791.py:22: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  immu_dur_df = immu_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/2461970791.py:22: FutureWarning: The frame.ap

In [76]:
final_cohort_immu = pd.merge(final_cohort, immu_dur_df, how = 'left', on = ['stay_id'])
final_cohort_immu_ant = pd.merge(final_cohort_immu, ant_dur_df, how = 'left', on = ['stay_id'])
final_cohort_immu_ant = pd.merge(final_cohort_immu_ant, ant_1stday, how = 'left', on = ['subject_id','hadm_id','stay_id'])

In [77]:
final_cohort_immu_ant[['immu_duration','ant_duration','ant_1stday']] = \
final_cohort_immu_ant[['immu_duration','ant_duration','ant_1stday']].fillna(0)

In [78]:
pd.pivot_table(data = final_cohort_immu_ant,values='stay_chart_included_mdr',index = ['immu_duration'],aggfunc= ['count','mean']).head(10)

count                    mean
              stay_chart_included_mdr stay_chart_included_mdr
immu_duration                                                
0.0                             42819                0.075037
1.0                               767                0.101695
2.0                               707                0.099010
3.0                               383                0.101828
4.0                               359                0.094708
5.0                               296                0.121622
6.0                               269                0.111524
7.0                               199                0.095477
8.0                               164                0.146341
9.0                               161                0.124224

In [79]:
pd.pivot_table(data = final_cohort_immu_ant,values='stay_chart_included_mdr',index = ['ant_duration'],aggfunc= ['count','mean']).head(10)

count                    mean
             stay_chart_included_mdr stay_chart_included_mdr
ant_duration                                                
0.0                            34985                0.078234
1.0                             3028                0.111625
2.0                             3292                0.063791
3.0                             1216                0.058388
4.0                              916                0.050218
5.0                              648                0.061728
6.0                              640                0.051562
7.0                              425                0.080000
8.0                              341                0.087977
9.0                              240                0.083333

In [80]:
pd.pivot_table(data = final_cohort_immu_ant,values='stay_chart_included_mdr',index = ['ant_1stday'],aggfunc= ['count','mean']).head(10)

count                    mean
           stay_chart_included_mdr stay_chart_included_mdr
ant_1stday                                                
0.0                          16812                0.043540
1.0                          30840                0.098898

## 住ICU第一天免疫抑制剂

In [81]:
immu_1stday = pd.merge(immu[['subject_id','hadm_id','starttime','stoptime']].drop_duplicates(),\
         final_cohort[['subject_id','hadm_id','stay_id','icu_intime']],how = 'right', on = ['subject_id','hadm_id'])

In [82]:
immu_1stday = immu_1stday[(((immu_1stday['icu_intime']-pd.to_timedelta(6,'hour'))<immu_1stday['starttime'])&\
                  (immu_1stday['starttime']<immu_1stday['icu_intime']+pd.to_timedelta(1,'day')))|\
                ((immu_1stday['starttime']<immu_1stday['icu_intime']) & (immu_1stday['icu_intime']<immu_1stday['stoptime']))]

In [83]:
immu_1stday['immu_1stday'] = 1
immu_1stday = immu_1stday[['stay_id','immu_1stday']]
final_cohort_immu_ant = pd.merge(final_cohort_immu_ant,immu_1stday,how = 'left', on = 'stay_id')
final_cohort_immu_ant['immu_1stday'] = final_cohort_immu_ant['immu_1stday'].fillna(0)

In [84]:
pd.pivot_table(data = final_cohort_immu_ant,values='stay_chart_included_mdr',index = ['immu_1stday'],aggfunc= ['count','mean']).head(10)

count                    mean
            stay_chart_included_mdr stay_chart_included_mdr
immu_1stday                                                
0.0                           41935                0.075784
1.0                           10380                0.111464

# 升压药

## 住ICU之前

In [85]:
vaso = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.vasopressor_hosp
''')

vaso.replace({'None':np.nan},inplace= True)

vaso['starttime'] = vaso['starttime'].apply(lambda x:trans_time(x))
vaso['stoptime'] = vaso['stoptime'].apply(lambda x:trans_time(x))

vaso['startdate'] = vaso['starttime'].dt.date
vaso['enddate'] = vaso['stoptime'].dt.date

vaso = vaso[vaso['starttime']<vaso['stoptime']]

trans_id(vaso)

vaso_co = pd.merge(vaso[['subject_id','hadm_id','starttime','stoptime']].drop_duplicates(),\
         final_cohort[['subject_id','hadm_id','stay_id','admittime','icu_intime']],how = 'left', on = ['subject_id','hadm_id'])

#限定在住ICU之前，本次住院期间
vaso_co = vaso_co[((vaso_co['starttime']-vaso_co['icu_intime']).dt.total_seconds()<0)&\
        ((vaso_co['starttime']-vaso_co['admittime']).dt.total_seconds()>-24*3600)]

vaso_co['endtime'] = vaso_co[['icu_intime','stoptime']].apply(lambda x: x[0] if x[0]<x[1] else x[1], axis = 1)

vaso_co['startdate']= vaso_co['starttime'].dt.date
vaso_co['enddate']= vaso_co['endtime'].dt.date

vaso_tocount = vaso_co[['subject_id','hadm_id','stay_id','startdate','enddate']].drop_duplicates()
vaso_tocount = vaso_tocount[~pd.isna(vaso_tocount['enddate'])]

def vaso_duration(df):
    days_list = []
    for i in range(df.size()):
        once_days = (df.loc[i,'enddate']-df.loc[i,'startdate']).days + 1
        for j in range(int(once_days)):
            mid_day = df.loc[i,'startdate'] + pd.to_timedelta(j,'day')
            days_list.append(mid_day)
    return len(list(set(days_list)))

vaso_dur_df = pd.DataFrame()
for i in set(vaso_tocount.stay_id):
    temp = pd.DataFrame()
    ini_df = vaso_tocount[vaso_tocount['stay_id'] == i].reset_index()
    days_list = []
    for j in range(len(ini_df)):
        once_days = (ini_df.loc[j,'enddate']-ini_df.loc[j,'startdate']).days + 1
        for m in range(once_days):
            mid_day = ini_df.loc[j,'startdate'] + pd.to_timedelta(m,'day')
            days_list.append(mid_day)
    temp.loc[0,'stay_id'] = i
    temp.loc[0,'vaso_duration'] = len(list(set(days_list)))
    vaso_dur_df = vaso_dur_df.append(temp,ignore_index=True)

/tmp/ipykernel_2822985/4183314373.py:55: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  vaso_dur_df = vaso_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/4183314373.py:55: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  vaso_dur_df = vaso_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/4183314373.py:55: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  vaso_dur_df = vaso_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/4183314373.py:55: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  vaso_dur_df = vaso_dur_df.append(temp,ignore_index=True)
/tmp/ipykernel_2822985/4183314373.py:55: FutureWarning: The frame.ap

In [86]:
final_cohort_immu_ant_vaso = pd.merge(final_cohort_immu_ant, vaso_dur_df, how = 'left', \
                                 on = ['stay_id'])
final_cohort_immu_ant_vaso['vaso_duration'].fillna(0,inplace = True)
final_cohort_immu_ant_vaso['vaso_beforeicu'] = final_cohort_immu_ant_vaso['vaso_duration'].apply(lambda x:1 if x>0 else 0)
final_cohort_immu_ant_vaso.drop(columns = ['vaso_duration'], inplace = True)

In [87]:
pd.pivot_table(data = final_cohort_immu_ant_vaso,values='stay_chart_included_mdr',index = ['vaso_beforeicu'],aggfunc= ['count','mean']).head(10)

count                    mean
               stay_chart_included_mdr stay_chart_included_mdr
vaso_beforeicu                                                
0                                49600                0.081653
1                                 2715                0.104972

## 住ICU第一天

In [88]:
vaso_1stday = pd.merge(vaso[['subject_id','hadm_id','starttime','stoptime']].drop_duplicates(),\
         final_cohort[['subject_id','hadm_id','stay_id','icu_intime']],how = 'right', on = ['subject_id','hadm_id'])

vaso_1stday = vaso_1stday[(((vaso_1stday['icu_intime']-pd.to_timedelta(6,'hour'))<vaso_1stday['starttime'])&\
                  (vaso_1stday['starttime']<vaso_1stday['icu_intime']+pd.to_timedelta(1,'day')))|\
                ((vaso_1stday['starttime']<vaso_1stday['icu_intime']) & (vaso_1stday['icu_intime']<vaso_1stday['stoptime']))]

vaso_1stday['vaso_1stday'] = 1
vaso_1stday = vaso_1stday[['stay_id','vaso_1stday']]

In [89]:
final_cohort_immu_ant_vaso = pd.merge(final_cohort_immu_ant_vaso,vaso_1stday,how = 'left', on = 'stay_id')
final_cohort_immu_ant_vaso['vaso_1stday'] = final_cohort_immu_ant_vaso['vaso_1stday'].fillna(0)

In [90]:
pd.pivot_table(data = final_cohort_immu_ant_vaso,values='stay_chart_included_mdr',index = ['vaso_1stday'],aggfunc= ['count','mean']).head(10)

count                    mean
            stay_chart_included_mdr stay_chart_included_mdr
vaso_1stday                                                
0.0                           33257                0.079953
1.0                           34235                0.085118

# 手术

In [91]:
surgical = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.service_surgical
''')

In [92]:
surgical['transfertime'] = surgical['transfertime'].apply(lambda x:trans_time(x))
trans_id(surgical)

In [93]:
surgical_simp = surgical[['hadm_id','surgical_prev','surgical_curr']].drop_duplicates()
surgical_simp['surgical'] = surgical_simp[['surgical_prev','surgical_curr']].apply(lambda x:1 if (x[0]=='1') or (x[1] == '1') else 0, axis = 1)

In [94]:
surgical_simp_sum = surgical_simp[['hadm_id','surgical']].drop_duplicates().groupby('hadm_id').sum().reset_index()#['surgical'].apply(lambda x:1 if x>=1 else 0)
surgical_fin = surgical_simp_sum
surgical_fin['surgical'] = surgical_fin['surgical'].apply(lambda x:1 if x>=1 else 0)

In [95]:
final_cohort_immu_ant_vaso_surg = pd.merge(final_cohort_immu_ant_vaso,surgical_fin,how = 'left', on = 'hadm_id')

# 置管

In [96]:
invasive_line = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.invasive_line
''')

In [97]:
trans_id(invasive_line)
invasive_line['starttime'] = invasive_line['starttime'].apply(trans_time)
invasive_line['endtime'] = invasive_line['endtime'].apply(trans_time)

In [98]:
invasive_line_mer = pd.merge(final_cohort_immu_ant_vaso_surg[['stay_id','icu_intime']],invasive_line,how = 'left', on = ['stay_id'])

In [99]:
invasive_line_mer_lim = invasive_line_mer[((invasive_line_mer['icu_intime']-pd.to_timedelta(6,'hour'))<invasive_line_mer['starttime'])&\
                  (invasive_line_mer['starttime']<invasive_line_mer['icu_intime']+pd.to_timedelta(1,'day'))]

In [100]:
invasive_line_mer_lim['invasive_line_1stday'] = 1
invasive_line_1stday = invasive_line_mer_lim[['stay_id','invasive_line_1stday']].drop_duplicates()

/tmp/ipykernel_2822985/1612464921.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  invasive_line_mer_lim['invasive_line_1stday'] = 1


In [101]:
final_cohort_immu_ant_vaso_surg_inv = pd.merge(final_cohort_immu_ant_vaso_surg,invasive_line_1stday,how = 'left', on = ['stay_id'])

In [102]:
final_cohort_immu_ant_vaso_surg_inv['invasive_line_1stday'].fillna(0,inplace = True)

In [103]:
pd.pivot_table(data = final_cohort_immu_ant_vaso_surg_inv,values='stay_chart_included_mdr',index = ['invasive_line_1stday'],aggfunc= ['count','mean'])

count                    mean
                     stay_chart_included_mdr stay_chart_included_mdr
invasive_line_1stday                                                
0.0                                    20817                0.071624
1.0                                    46675                0.087456

# 机械通气

In [104]:
ventilation = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.ventilation
''')

trans_id(ventilation)
ventilation['starttime'] = ventilation['starttime'].apply(trans_time)
ventilation['endtime'] = ventilation['endtime'].apply(trans_time)

ventilation_mer = pd.merge(final_cohort[['stay_id','icu_intime']],ventilation,how = 'left', on = ['stay_id'])

ventilation_mer_lim = ventilation_mer[((ventilation_mer['icu_intime']-pd.to_timedelta(6,'hour'))<ventilation_mer['starttime'])&\
                  (ventilation_mer['starttime']<ventilation_mer['icu_intime']+pd.to_timedelta(1,'day'))]

ventilation_mer_lim['ventilation_1stday'] = 1
ventilation_1stday = ventilation_mer_lim[['stay_id','ventilation_1stday']].drop_duplicates()

final_cohort_immu_ant_vaso_surg_inv_vent = pd.merge(final_cohort_immu_ant_vaso_surg_inv,ventilation_1stday,how = 'left', on = ['stay_id'])

final_cohort_immu_ant_vaso_surg_inv_vent['ventilation_1stday'].fillna(0,inplace = True)

/tmp/ipykernel_2822985/4051615661.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ventilation_mer_lim['ventilation_1stday'] = 1


In [105]:
pd.pivot_table(data = final_cohort_immu_ant_vaso_surg_inv_vent,values='stay_chart_included_mdr',index = ['ventilation_1stday'],aggfunc= ['count','mean'])

count                    mean
                   stay_chart_included_mdr stay_chart_included_mdr
ventilation_1stday                                                
0.0                                  11974                0.075413
1.0                                  55518                0.084117

# CRRT

In [106]:
crrt = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.crrt
''')

trans_id(crrt)
crrt['charttime'] = crrt['charttime'].apply(trans_time)

crrt_mer = pd.merge(final_cohort[['stay_id','icu_intime']],crrt,how = 'left', on = ['stay_id'])

crrt_mer_lim = crrt_mer[((crrt_mer['icu_intime']-pd.to_timedelta(6,'hour'))<crrt_mer['charttime'])&\
                  (crrt_mer['charttime']<crrt_mer['icu_intime']+pd.to_timedelta(1,'day'))]

crrt_mer_lim['crrt_1stday'] = 1
crrt_1stday = crrt_mer_lim[['stay_id','crrt_1stday']].drop_duplicates()

/tmp/ipykernel_2822985/1338224003.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  crrt_mer_lim['crrt_1stday'] = 1


In [107]:
final_cohort_immu_ant_vaso_surg_inv_vent_crrt = pd.merge(final_cohort_immu_ant_vaso_surg_inv_vent,crrt_1stday,how = 'left', on = ['stay_id'])

final_cohort_immu_ant_vaso_surg_inv_vent_crrt['crrt_1stday'].fillna(0,inplace = True)

# 评分

In [108]:
lods = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.lods
''')

In [109]:
sofa = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.first_day_sofa
''')

In [110]:
sirs = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.sirs
''')

In [111]:
apsiii = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.apsiii
''')

In [112]:
oasis = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.oasis
''')

In [113]:
sapsii = get_data_MIMIC('''
set search_path to mimiciv;
select stay_id,sapsii
from mimiciv_derived.sapsii
''')

In [114]:
trans_float(lods)
trans_float(sofa)
trans_float(sirs)
trans_float(apsiii)
trans_float(oasis)
trans_float(sapsii)

In [115]:
scores = lods[['stay_id','lods']].merge(sofa[['stay_id','sofa']],how = 'left', on = 'stay_id').\
merge(sirs[['stay_id','sirs']],how = 'left', on = 'stay_id').\
merge(apsiii[['stay_id','apsiii']],how = 'left', on = 'stay_id').\
merge(oasis[['stay_id','oasis']],how = 'left', on = 'stay_id').\
merge(sapsii[['stay_id','sapsii']],how = 'left', on = 'stay_id')

In [116]:
final_cohort_immu_ant_vaso_surg_inv_vent_crrt_scores = pd.merge(final_cohort_immu_ant_vaso_surg_inv_vent_crrt,scores,how = 'left', on = ['stay_id'])

# 合并症

In [117]:
charlson = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.charlson
''')

In [118]:
trans_float(charlson)

# 抗生素种类

In [119]:
ant_trans = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.antibiotic_trans
''')

In [120]:
trans_float(ant_trans)

In [121]:
ant_trans[pd.isna(ant_trans['amoxicill'])]

Empty DataFrame
Columns: [hadm_id, amikacin, amoxicill, amoxicillin_clavulanate, ampicillin, ampicillin_sulbactam, azithromycin, aztreonam, cefuroxime_axetil, bactrim, cefazolin, ceftazidime, ceftazidime_avibactam, cefadroxil, cefepime, cefotaxime, ceftaroline, ceftriaxone, cephalexin, chloramphenicol, ciprofloxacin, clarithromycin, clindamycin, daptomycin, dicloxacillin, doxycycline, erythromycin, gentamicin, cefalexin, levofloxacin, linezolid, nitrofurantoin, metronidazole, meropenem, imipenem, ertapenem, minocycline, moxifloxacin, mupirocin, nafcillin, neomycin_polymyxin, ofloxacin, oxacillin, penicillin, piperacillin_tazobactam, ceftolozane_tazobactam, rifampin, sulfadiazine, polymyxin_trimethoprim, sulfameth_trimethoprim, tetracycline, tobramycin, vancomycin]
Index: []

# admission type

In [122]:
ad_loc = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_hosp.admissions
''')

In [123]:
ad_loc_loc = ad_loc[['hadm_id','admission_location']]

In [124]:
trans_id(ad_loc_loc)

/tmp/ipykernel_2822985/1820869256.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[i] = df[i].astype(float)


In [125]:
ad_loc_trans = pd.get_dummies(ad_loc_loc, columns = ['admission_location'])

In [126]:
ad_loc_trans

hadm_id  admission_location_AMBULATORY SURGERY TRANSFER  \
0       22580355.0                                               0   
1       23440765.0                                               0   
2       27635105.0                                               0   
3       29771935.0                                               0   
4       21736423.0                                               0   
...            ...                                             ...   
431226  28440971.0                                               0   
431227  27417763.0                                               0   
431228  27672872.0                                               0   
431229  27475401.0                                               0   
431230  20668418.0                                               0   

        admission_location_CLINIC REFERRAL  admission_location_EMERGENCY ROOM  \
0                                        0                                  0   
1                                        0                                  0   
2                                        0                                  1   
3                                        0                                  0   
4                                        0                                  1   
...                                    ...                                ...   
431226                                   0                                  0   
431227                                   0                                  1   
431228                                   0                                  1   
431229                                   0                                  0   
431230                                   0                                  0   

        admission_location_INFORMATION NOT AVAILABLE  \
0                                                  0   
1                                                  0   
2                                                  0   
3                                                  0   
4                                                  0   
...                                              ...   
431226                                             0   
431227                                             0   
431228                                             0   
431229                                             0   
431230                                             0   

        admission_location_INTERNAL TRANSFER TO OR FROM PSYCH  \
0                                                       0       
1                                                       0       
2                                                       0       
3                                                       0       
4                                                       0       
...                                                   ...       
431226                                                  0       
431227                                                  0       
431228                                                  0       
431229                                                  0       
431230                                                  0       

        admission_location_PACU  admission_location_PHYSICIAN REFERRAL  \
0                             0                                      0   
1                             0                                      1   
2                             0                                      0   
3                             0                                      0   
4                             0                                      0   
...                         ...                                    ...   
431226                        0                                      1   
431227                        0                                      0   
431228                        0                                      0   
431

# 身高体重

In [127]:
height = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.height_1sttime
''')

In [128]:
weight = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.weight_1sttime
''')

In [129]:
trans_id(height)
trans_id(weight)

# 营养

In [130]:
nutrition = get_data_MIMIC('''
set search_path to mimiciv;
select *
from mimiciv_derived.first_day_nutrition
''')

In [131]:
trans_id(nutrition)

# 既往史

## 体重减轻10磅

In [132]:
weight_loss = get_data_MIMIC('''
select * 
from mimiciv_derived.history_weight_loss
''')

In [133]:
trans_float(weight_loss)

In [134]:
weight_loss = weight_loss.groupby('stay_id').sum().reset_index()

for i in weight_loss.columns[1:]:
    weight_loss[i] = weight_loss[i].apply(lambda x:1 if x>0 else 0)

## 辅助方式

In [135]:
assistive_devices = get_data_MIMIC('''
select * 
from mimiciv_derived.history_assistive_devices
''')

In [136]:
trans_id(assistive_devices)

In [137]:
assistive_devices = pd.merge(final_cohort['stay_id'], assistive_devices, how = 'left', on = ['stay_id']).fillna('None')

In [138]:
assistive_devices = pd.get_dummies(assistive_devices,columns = ['history_assistive_devices']).drop_duplicates()

In [139]:
assistive_devices = assistive_devices.groupby('stay_id').sum().reset_index()

for i in assistive_devices.columns[1:]:
    assistive_devices[i] = assistive_devices[i].apply(lambda x:1 if x>0 else 0)

## 疼痛

In [140]:
pain = get_data_MIMIC('''
select * 
from mimiciv_derived.history_currently_pain
''')

In [141]:
trans_float(pain)

In [142]:
pain = pain.groupby('stay_id').sum().reset_index()

for i in pain.columns[1:]:
    pain[i] = pain[i].apply(lambda x:1 if x>0 else 0)

## 透析

In [143]:
dialysis = get_data_MIMIC('''
select * 
from mimiciv_derived.history_dialysis
''')

In [144]:
trans_float(dialysis)

In [145]:
dialysis = dialysis.groupby('stay_id').sum().reset_index()

for i in dialysis.columns[1:]:
    dialysis[i] = dialysis[i].apply(lambda x:1 if x>0 else 0)

## 吞咽困难

In [146]:
difficulty_swallowing = get_data_MIMIC('''
select * 
from mimiciv_derived.history_difficulty_swallowing
''')

In [147]:
trans_float(difficulty_swallowing)

In [148]:
difficulty_swallowing = difficulty_swallowing.groupby('stay_id').sum().reset_index()

for i in difficulty_swallowing.columns[1:]:
    difficulty_swallowing[i] = difficulty_swallowing[i].apply(lambda x:1 if x>0 else 0)

## 静脉

In [149]:
IV_access = get_data_MIMIC('''
select * 
from mimiciv_derived.history_IV_access
''')

In [150]:
trans_float(IV_access)

In [151]:
IV_access = IV_access.groupby('stay_id').sum().reset_index()

for i in IV_access.columns[1:]:
    IV_access[i] = IV_access[i].apply(lambda x:1 if x>0 else 0)

## 既往疾病

In [152]:
history_past = get_data_MIMIC('''
select * 
from mimiciv_derived.history_past
''')

In [153]:
trans_id(history_past)

In [154]:
history_past = pd.get_dummies(history_past,columns = ['history_past']).drop_duplicates()

In [155]:
history_past = history_past.groupby('stay_id').sum().reset_index()

In [156]:
history_past.columns[1:]

Index(['history_past_Anemia', 'history_past_Asthma', 'history_past_COPD',
       'history_past_Diabetes - Insulin', 'history_past_Diabetes - Oral Agent',
       'history_past_ETOH', 'history_past_GI Bleed', 'history_past_HEMO or PD',
       'history_past_Hepatitis', 'history_past_Liver Failure',
       'history_past_Pancreatitis', 'history_past_Renal Failure',
       'history_past_Seizures', 'history_past_Smoker'],
      dtype='object')

In [157]:
for i in history_past.columns[1:]:
    history_past[i] = history_past[i].apply(lambda x:1 if x>0 else 0)

## 既往心血管疾病

In [158]:
history_past_cv = get_data_MIMIC('''
select * 
from mimiciv_derived.history_CV
''')

In [159]:
trans_id(history_past_cv)

In [160]:
history_past_cv = pd.get_dummies(history_past_cv,columns = ['history_cv']).drop_duplicates()

In [161]:
history_past_cv = history_past_cv.groupby('stay_id').sum().reset_index()

for i in history_past_cv.columns[1:]:
    history_past_cv[i] = history_past_cv[i].apply(lambda x:1 if x>0 else 0)

# 标本采集

In [162]:
culture_samples = get_data_MIMIC('''
select *
from mimiciv_derived.first_day_culture
''')

In [163]:
trans_float(culture_samples)

In [164]:
culture_samples = culture_samples.groupby('stay_id').sum().reset_index()

for i in culture_samples.columns[1:]:
    culture_samples[i] = culture_samples[i].apply(lambda x:1 if x>0 else 0)

## 既往和标本整合

In [165]:
hist_samp = weight_loss.merge(assistive_devices,how = 'outer', on = 'stay_id').\
merge(pain, how = 'outer', on = 'stay_id').\
merge(dialysis, how = 'outer', on = 'stay_id').\
merge(difficulty_swallowing, how = 'outer', on = 'stay_id').\
merge(IV_access, how = 'outer', on = 'stay_id').\
merge(history_past, how = 'outer', on = 'stay_id').\
merge(history_past_cv, how = 'outer', on = 'stay_id').\
merge(culture_samples, how = 'outer', on = 'stay_id')

In [166]:
hist_samp = hist_samp.astype(float).fillna(0)

In [167]:
hist_samp[hist_samp.duplicated(subset = ['stay_id'],keep = False)]

Empty DataFrame
Columns: [stay_id, history_unintentional_weight_loss_10_lbs, history_assistive_devices_Cane, history_assistive_devices_None, history_assistive_devices_Other, history_assistive_devices_Walker, history_assistive_devices_Wheelchair, history_currently_pain, history_dialysis, history_difficulty_swallowing, history_iv_access, history_past_Anemia, history_past_Asthma, history_past_COPD, history_past_Diabetes - Insulin, history_past_Diabetes - Oral Agent, history_past_ETOH, history_past_GI Bleed, history_past_HEMO or PD, history_past_Hepatitis, history_past_Liver Failure, history_past_Pancreatitis, history_past_Renal Failure, history_past_Seizures, history_past_Smoker, history_cv_Angina, history_cv_Arrhythmias, history_cv_CAD, history_cv_CHF, history_cv_CVA, history_cv_Hypertension, history_cv_MI, history_cv_PVD, history_cv_Pacemaker, nasal_swab, blood_culture, urine_culture, sputum_culture, stool_culture, pan_culture, bal_fluid_culture, wound_culture, rectal_swab, csf_culture]
Index: []

In [168]:
icustay = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_icu.icustays
''')

In [169]:
admission = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_hosp.admissions
''')

In [170]:
trans_id(icustay)

In [171]:
trans_id(admission)

# 表连接

In [172]:
final_cohort_immu_ant_vaso_surg_inv_vent_crrt_scores = final_cohort_immu_ant_vaso_surg_inv_vent_crrt_scores.merge(icustay[['stay_id','first_careunit','last_careunit']], how = 'left', on = 'stay_id').\
merge(admission[['hadm_id','admission_type']], how = 'left', on = 'hadm_id')

In [173]:
stage1 = pd.merge(final_cohort_immu_ant_vaso_surg_inv_vent_crrt_scores,charlson,how = 'left', on = ['subject_id','hadm_id'])

In [174]:
stage1 = stage1.drop_duplicates()

In [175]:
lab_vs_fc.columns

Index(['stay_id', 'albumin', 'globulin', 'total_protein', 'aniongap',
       'bicarbonate_x', 'bun', 'calcium_x', 'chloride_x', 'creatinine',
       'glucose_x', 'sodium_x', 'potassium_x', 'aado2', 'baseexcess',
       'bicarbonate_y', 'totalco2', 'carboxyhemoglobin', 'chloride_y',
       'calcium_y', 'glucose_y', 'hematocrit_x', 'hemoglobin_x', 'lactate',
       'methemoglobin', 'o2flow', 'fio2', 'so2', 'pco2', 'peep', 'ph', 'po2',
       'potassium_y', 'requiredo2', 'sodium_y', 'temperature_x', 'comments',
       'specimen_id', 'wbc_x', 'basophils_abs', 'eosinophils_abs',
       'lymphocytes_abs', 'monocytes_abs', 'neutrophils_abs', 'basophils',
       'eosinophils', 'lymphocytes', 'monocytes', 'neutrophils',
       'atypical_lymphocytes', 'bands', 'immature_granulocytes',
       'metamyelocytes', 'nrbc', 'bleeding_time', 'd_dimer', 'fibrinogen',
       'thrombin', 'inr', 'pt', 'ptt', 'hematocrit_y', 'hemoglobin_y', 'mch',
       'mchc', 'mcv', 'platelet', 'rbc', 'rdw', 'wbc_y', 'tro

In [176]:
stage2 = pd.merge(stage1,lab_vs_fc,how = 'left', on = ['stay_id']).drop_duplicates()

In [177]:
stage3 = stage2.merge(ant_trans, how = 'left', on = ['hadm_id']).merge(ad_loc_trans, how = 'left', on = ['hadm_id'])

In [178]:
stage3 = stage3.merge(height, how = 'left', on = ['stay_id']).merge(weight, how = 'left', on = ['stay_id'])

In [179]:
stage3 = stage3.merge(nutrition, how = 'left', on = ['stay_id'])

In [180]:
stage3 = stage3.merge(hist_samp, how = 'left', on = ['stay_id'])

In [181]:
stage3 = stage3.merge(adm_pre90,how = 'left', on = ['hadm_id'])
stage3['before_adm_90d'] = stage3['before_adm_90d'].fillna(0)

In [182]:
stage3[['ent_nut','par_nut']] = stage3[['ent_nut','par_nut']].astype(float).fillna(0)

In [183]:
stage3 = stage3.drop_duplicates(subset = ['stay_id'], keep = 'first')

In [184]:
pd.pivot_table(data = stage3,values='stay_chart_included_mdr',index = ['csf_culture'],aggfunc= ['count','mean'])

count                    mean
            stay_chart_included_mdr stay_chart_included_mdr
csf_culture                                                
0.0                           47621                0.079356
1.0                              31                0.096774

In [185]:
stage_sup = get_data_MIMIC('''
set search_path to mimiciv;
select * 
from mimiciv_derived.lab_sup_nea
''')

In [186]:
stage_sup.replace({'None':np.nan},inplace= True)

In [187]:
trans_id(stage_sup)
stage3 = stage3.merge(stage_sup,how = 'left', on = ['stay_id'])

In [188]:
stage3.columns.to_list()

['subject_id',
 'hadm_id',
 'stay_id',
 'gender',
 'admittime',
 'dischtime',
 'los_hospital',
 'admission_age',
 'race',
 'hospital_expire_flag',
 'hospstay_seq',
 'first_hosp_stay',
 'icu_intime',
 'icu_outtime',
 'los_icu',
 'icustay_seq',
 'first_icu_stay',
 'spec_type_desc_URINE',
 'spec_type_desc_BLOOD CULTURE',
 'spec_type_desc_SWAB',
 'spec_type_desc_SPUTUM',
 'spec_type_desc_TISSUE',
 'spec_type_desc_BRONCHOALVEOLAR LAVAGE',
 'spec_type_desc_ABSCESS',
 'firsthospmdrcharttime',
 'firsthospmdrstoretime',
 'firsthospmdrorgname',
 'firsthospmdrRAB',
 'last',
 'previous_mdrpos_lessthan14d',
 'previous_mdrneg_lessthan14d',
 'previous_mdrpos_lessthan90d',
 'previous_mdrneg_lessthan90d',
 'stay_chart_included',
 'stay_chart_included_mdr',
 'stay_chart_included_mdr_neg_tot',
 'stay_chart_included_mdr_pos_tot',
 'icustay_rank',
 'los_icu_exc',
 'los_hosp_beforeicu',
 'immu_duration',
 'ant_duration',
 'ant_1stday',
 'immu_1stday',
 'vaso_beforeicu',
 'vaso_1stday',
 'surgical',
 'invasi

In [189]:
stage3.to_csv('data_tomodel_1st_revise2.csv', index = False)

In [190]:
cohort_total_acty = pd.read_csv('mdro_tomice.csv')

In [191]:
act_year_ind = pd.pivot_table(data = cohort_total_acty,values='stay_chart_included_mdr',\
               index = ['actual_year_group'],aggfunc= ['count','mean']).index.to_list()
act_year_pre = act_year_ind[0:7]
act_year_lat = act_year_ind[-4:]

In [192]:
train_df = cohort_total_acty[cohort_total_acty['actual_year_group'].isin(act_year_pre)]
val_df = cohort_total_acty[cohort_total_acty['actual_year_group'].isin(act_year_lat)]

In [193]:
mdro = pd.concat([train_df,val_df])

In [194]:
mdro = mdro[['stay_id','actual_year_group']].merge(stage3, how = 'left', on = ['stay_id'])

In [195]:
# 假设mdro是你的DataFrame
mdro['weight'] = pd.to_numeric(mdro['weight'], errors='coerce')
mdro['height'] = pd.to_numeric(mdro['height'], errors='coerce')

# 计算BMI
mdro['bmi'] = mdro['weight'] / (mdro['height'] ** 2)


In [196]:
(100-pd.isna(mdro).sum()*100/mdro.shape[0]).sort_values()[:60]

troponin_i                0.000000
mpv                       0.000000
fio2                      0.000000
comments                  0.000000
thrombin                  0.309716
d_dimer                   0.415083
ggt                       1.242058
globulin                  2.330853
methemoglobin             2.544781
carboxyhemoglobin         2.803410
total_protein             3.767681
crp                       3.997573
bilirubin_indirect        6.746703
nrbc                      6.906351
bilirubin_direct          7.040455
aado2                     9.112679
requiredo2                9.128644
amylase                   9.502219
bicarbonate_y             9.585236
firsthospmdrorgname      11.849037
firsthospmdrRAB          11.849037
firsthospmdrcharttime    11.849037
firsthospmdrstoretime    11.849037
ntprobnp                 15.683770
peep                     18.177464
atypical_lymphocytes     19.687729
metamyelocytes           20.051726
bands                    21.574763
o2flow              

In [197]:
(100-pd.isna(mdro).sum()*100/mdro.shape[0]).sort_values()[60:120]

lactate                    81.682046
ptt                        95.711868
calcium_x                  95.897059
inr                        96.018391
pt                         96.018391
phosphate                  96.047128
temperature_y              97.314729
mg                         98.049108
weight                     98.502506
gcs_motor                  98.524857
gcs_verbal                 99.118746
gcs_eyes                   99.559373
resp_rate                  99.610460
dbp                        99.645583
sbp                        99.658354
mbp                        99.744564
spo2                       99.849931
gcs                        99.862703
gcs_unable                 99.862703
heart_rate                 99.875475
mupirocin                  99.904212
moxifloxacin               99.904212
minocycline                99.904212
ertapenem                  99.904212
metronidazole              99.904212
meropenem                  99.904212
nafcillin                  99.904212
l

In [198]:
(100-pd.isna(mdro).sum()*100/mdro.shape[0]).sort_values()[120:150]

cefotaxime         99.904212
ceftaroline        99.904212
ceftriaxone        99.904212
cephalexin         99.904212
chloramphenicol    99.904212
ciprofloxacin      99.904212
clarithromycin     99.904212
clindamycin        99.904212
daptomycin         99.904212
dicloxacillin      99.904212
amoxicill          99.904212
aztreonam          99.904212
eosinophils        99.932948
neutrophils        99.936141
basophils          99.936141
neutrophils_abs    99.936141
monocytes_abs      99.936141
eosinophils_abs    99.936141
basophils_abs      99.936141
monocytes          99.936141
aniongap           99.952106
rdw                99.964878
mch                99.971263
mchc               99.980842
hemoglobin_y       99.984035
mcv                99.984035
platelet           99.984035
rbc                99.987228
potassium_x        99.990421
glucose_x          99.990421
dtype: float64

In [199]:
(100-pd.isna(mdro).sum()*100/mdro.shape[0]).sort_values()[150:210]

creatinine                                                    99.990421
bun                                                           99.990421
bicarbonate_x                                                 99.993614
chloride_x                                                    99.993614
sodium_x                                                      99.996807
history_assistive_devices_Cane                               100.000000
history_assistive_devices_None                               100.000000
history_assistive_devices_Other                              100.000000
history_assistive_devices_Walker                             100.000000
history_assistive_devices_Wheelchair                         100.000000
history_currently_pain                                       100.000000
history_dialysis                                             100.000000
hematocrit_y                                                 100.000000
history_iv_access                                            100

In [200]:
(100-pd.isna(mdro).sum()*100/mdro.shape[0]).sort_values()[210:260]

history_past_Renal Failure     100.0
history_past_Seizures          100.0
history_past_Smoker            100.0
history_past_GI Bleed          100.0
history_cv_Angina              100.0
history_cv_CAD                 100.0
history_cv_CHF                 100.0
history_cv_CVA                 100.0
history_cv_Hypertension        100.0
history_cv_MI                  100.0
history_cv_PVD                 100.0
history_cv_Arrhythmias         100.0
hospital_expire_flag           100.0
icu_outtime                    100.0
first_hosp_stay                100.0
sirs                           100.0
apsiii                         100.0
oasis                          100.0
sapsii                         100.0
first_careunit                 100.0
last_careunit                  100.0
admission_type                 100.0
age_score                      100.0
myocardial_infarct             100.0
congestive_heart_failure       100.0
peripheral_vascular_disease    100.0
cerebrovascular_disease        100.0
d